In [ ]:
import pandas as pd

pd.set_option('display.max_rows', 100)
pd.set_option('display.max_columns', None)

import os
from VAERSFileDownloader import updateVAERSFiles
from datetime import datetime
from DateProvider import DateProvider
from InternationalVaersCovid19Provider import getInternationalVaersCovid19, get_international_VAERSVAX_VAERSSYMPTOMS_Covid19
from BatchCodeTableHtmlUpdater import updateBatchCodeTableHtmlFile
from BatchCodeTablePersister import createAndSaveBatchCodeTables
from SymptomByBatchcodeTableFactory import SymptomByBatchcodeTableFactory
from HistogramFactoryAndPersister import createAndSaveGlobalHistograms, createAndSaveHistogramsForCountries

In [ ]:
print(datetime.now().strftime("%d.%m.%Y, %H:%M:%S Uhr"))

In [ ]:
dateProvider = DateProvider()
print('          lastUpdated:', dateProvider.getLastUpdated())
print('lastUpdatedDataSource:', dateProvider.getLastUpdatedDataSource())
needsUpdate = dateProvider.needsUpdate()
print('needsUpdate:', needsUpdate)

In [ ]:
years_from_start_of_COVID_vaccination_to_present = list(range(2020, datetime.now().year + 1))

In [ ]:
updateVAERSFiles(
        years = years_from_start_of_COVID_vaccination_to_present,
        workingDirectory = os.getcwd())

In [ ]:
international_VAERSVAX_Covid19, international_VAERSSYMPTOMS = get_international_VAERSVAX_VAERSSYMPTOMS_Covid19(years = years_from_start_of_COVID_vaccination_to_present)

In [ ]:
international_VAERSVAX_Covid19

In [ ]:
international_VAERSSYMPTOMS

In [ ]:
symptomByBatchcodeTable = SymptomByBatchcodeTableFactory.createSymptomByBatchcodeTable(international_VAERSVAX_Covid19, international_VAERSSYMPTOMS)
symptomByBatchcodeTable

In [ ]:
createAndSaveGlobalHistograms(symptomByBatchcodeTable)

In [ ]:
createAndSaveHistogramsForCountries(symptomByBatchcodeTable)

In [ ]:
internationalVaersCovid19 = getInternationalVaersCovid19(years = years_from_start_of_COVID_vaccination_to_present)
internationalVaersCovid19

In [ ]:
updateBatchCodeTableHtmlFile(internationalVaersCovid19, batchCodeTableHtmlFile="../docs/batchCodeTable.html")

In [ ]:
createAndSaveBatchCodeTables(
    internationalVaersCovid19,
    minADRsForLethality = 100,
    onCountryProcessed = display)

# Vaccine Distribution by Zipcode

In [ ]:
vaccineDistributionByZipcode  = pd.read_excel(
        io = 'tmp/Amended-22-01962-Pfizer-2022-0426-pulled-2022-0823.xlsx',
        usecols = ['PROVIDER_NAME', 'ZIPCODE_SHP', 'LOT_NUMBER', 'DOSES_SHIPPED'])
vaccineDistributionByZipcode

In [ ]:
from VaccineDistributionByZipcodeSimplifier import VaccineDistributionByZipcodeSimplifier

vaccineDistributionByZipcode = VaccineDistributionByZipcodeSimplifier.sumDoses(vaccineDistributionByZipcode)
vaccineDistributionByZipcode

In [ ]:
from ADR_by_Batchcode_Table_Factory import create_ADR_by_Batchcode_Table_4USA

ADR_by_Batchcode_Table_4USA = create_ADR_by_Batchcode_Table_4USA(internationalVaersCovid19)
ADR_by_Batchcode_Table_4USA

In [ ]:
from ADRColumnAdder import ADRColumnAdder

vaccineDistributionByZipcode = ADRColumnAdder(ADR_by_Batchcode_Table_4USA).addADRColumn(vaccineDistributionByZipcode)
vaccineDistributionByZipcode

In [ ]:
vaccineDistributionByZipcode.to_excel('tmp/Amended-22-01962-Pfizer-2022-0426-pulled-2022-0823_sumDoses.xlsx')

In [ ]:
from IOUtils import IOUtils

IOUtils.saveDataFrameAsJson(vaccineDistributionByZipcode, '../docs/data/vaccineDistributionByZipcode/VaccineDistributionByZipcode.json')